In [1]:
import cv2
import os
import mediapipe as mp
import numpy as np
from matplotlib import pyplot as plt
import time
mp_drawing = mp.solutions.drawing_utils
mp_pose = mp.solutions.pose # Holistic model

In [2]:
def mediapipe_detection(image, model):
    image = cv2.cvtColor(frame,cv2.COLOR_BGR2RGB)
    image.flags.writeable = False

    results=model.process(image)

    image.flags.writeable = True
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
    return image, results

In [3]:
def draw_landmarks(image, results):

    mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_pose.POSE_CONNECTIONS) # Draw pose connections


In [60]:
def extract_keypoints(results):
    pose = np.array([[res.x, res.y, res.z] for res in results.pose_landmarks.landmark]).flatten() if results.pose_landmarks else np.zeros(33*3)
    if len(pose) != 99:
    # Use numpy.pad() to add zeros at the end
        padded_array = np.pad(pose, (0, 99-len(pose)), 'constant')
    else:
        # No zeros need to be added
        padded_array = pose
    return padded_array


In [5]:
# Path for exported data, numpy arrays
DATA_PATH = os.path.join('MP_Data') 

# Actions that we try to detect
actions = np.array(['hello', 'thanks', 'iloveyou'])

# Thirty videos worth of data
no_sequences = 30

# Videos are going to be 30 frames in length
sequence_length = 30

# Folder start
start_folder = 30

In [9]:
for action in actions: 
    #dirmax = np.max(np.array(os.listdir(os.path.join(DATA_PATH, action))).astype(int))
    for sequence in range(1,no_sequences+1):
        try: 
            os.makedirs(os.path.join(DATA_PATH, action, str(sequence)))
        except:
            pass

In [61]:
cap = cv2.VideoCapture(0)
# Set mediapipe model 
with mp_pose.Pose(min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
    
    # NEW LOOP
    # Loop through actions
    for action in actions:
        # Loop through sequences aka videos
        for sequence in range(1, start_folder+1):
            # Loop through video length aka sequence length
        
            for frame_num in range(sequence_length):

                # Read feed
                ret, frame = cap.read()

                # Make detections
                image, results = mediapipe_detection(frame, pose)
                
                # Draw landmarks
                draw_landmarks(image, results)
                
                # NEW Apply wait logic
                if frame_num == 0: 
                    cv2.putText(image, 'STARTING COLLECTION', (120,200), 
                               cv2.FONT_HERSHEY_SIMPLEX, 1, (0,255, 0), 4, cv2.LINE_AA)
                    cv2.putText(image, 'Collecting frames for {} Video Number {}'.format(action, sequence), (15,12), 
                               cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                    # Show to screen
                    cv2.imshow('OpenCV Feed', image)
                    cv2.waitKey(500)
                else: 
                    cv2.putText(image, 'Collecting frames for {} Video Number {}'.format(action, sequence), (15,12), 
                               cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 0, 255), 1, cv2.LINE_AA)
                    # Show to screenqqq
                    cv2.imshow('OpenCV Feed', image)
                
                # NEW Export keypoints
                keypoints = extract_keypoints(results)
                print("-------KEYPOINTS------------")
                print(keypoints.shape)
                print("-------KEYPOINTS------------")
                npy_path = os.path.join(DATA_PATH, action, str(sequence), str(frame_num))
                np.save(npy_path, keypoints)

                # Break gracefully
                if cv2.waitKey(10) & 0xFF == ord('q'):
                    break
                    
    cap.release()
    cv2.destroyAllWindows()

-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-------KEYPOINTS------------
-------KEYPOINTS------------
(99,)
-----

In [13]:
from sklearn.model_selection import train_test_split
from tensorflow.keras.utils import to_categorical

In [14]:
label_map = {label:num for num, label in enumerate(actions)}

In [62]:
sequences, labels = [], []
for action in actions:
    for sequence in np.array(os.listdir(os.path.join(DATA_PATH, action))).astype(int):
        window = []
        for frame_num in range(sequence_length):
            res = np.load(os.path.join(DATA_PATH, action, str(sequence), "{}.npy".format(frame_num)))
            if len(res)!=132:
                print("WTF: ",len(res) )
                print(res)
             
            window.append(res)
        sequences.append(window)
        labels.append(label_map[action])

WTF:  99
[ 0.44588169  0.63261986 -0.55713147  0.46620855  0.57857704 -0.52195692
  0.48060593  0.57624614 -0.52169865  0.49375993  0.57457858 -0.52153879
  0.41834611  0.59235168 -0.51945519  0.40272695  0.5986948  -0.51884604
  0.38744432  0.60594743 -0.51904619  0.51579404  0.59862113 -0.29493153
  0.36872196  0.63995522 -0.27156755  0.47769803  0.68955618 -0.47192937
  0.42188263  0.70376354 -0.46484795  0.6432727   0.88861412 -0.18732056
  0.28393796  0.91982323 -0.23557106  0.70998824  1.22082114 -0.22404137
  0.26370952  1.25537038 -0.33264622  0.69634175  1.46877337 -0.43255895
  0.28200489  1.50726473 -0.79082882  0.72521913  1.55576777 -0.50636232
  0.25433591  1.60561383 -0.89577311  0.67988127  1.55826306 -0.53966451
  0.29882139  1.60000789 -0.93683398  0.66261053  1.52131665 -0.46073079
  0.31615442  1.55792618 -0.82705325  0.602485    1.49113882 -0.0298527
  0.36062142  1.51106262  0.03485412  0.60605657  1.98889899  0.02230456
  0.39077294  2.00192618  0.08431444  0.616

In [25]:
print(len(sequences))

90


In [75]:
X = np.array(sequences)
print(X.shape)

(90, 30, 99)


In [76]:
y = to_categorical(labels).astype(int)

In [66]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.05)

In [ ]:
from sklearn.model_selection import cross_val_score
k_folds = 5
k_choices = [1, 3, 5, 8, 10, 12, 15, 20, 50, 100]
scores = np.zeros((len(k_choices), k_folds))

In [38]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from tensorflow.keras.callbacks import TensorBoard

In [39]:
log_dir = os.path.join('Logs')
tb_callback = TensorBoard(log_dir=log_dir)

In [67]:
model = Sequential()
model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(30,99)))
model.add(LSTM(128, return_sequences=True, activation='relu'))
model.add(LSTM(64, return_sequences=False, activation='relu'))
model.add(Dense(64, activation='relu'))
model.add(Dense(32, activation='relu'))
model.add(Dense(actions.shape[0], activation='softmax'))

In [68]:
model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['categorical_accuracy'])

In [ ]:
from keras.callbacks import ModelCheckpoint
from sklearn.model_selection import KFold, StratifiedKFold
kf = KFold(n_splits = 5, shuffle=True)
acc_per_fold = []
loss_per_fold = []
checkpoint = ModelCheckpoint("best_model.h5", monitor='val_categorical_accuracy', verbose=1, save_best_only=True, mode='max')
fold_no = 1
for train, test in kf.split(X, y):
    model = Sequential()
    model.add(LSTM(64, return_sequences=True, activation='relu', input_shape=(30,99)))
    model.add(LSTM(128, return_sequences=True, activation='relu'))
    model.add(LSTM(64, return_sequences=False, activation='relu'))
    model.add(Dense(64, activation='relu'))
    model.add(Dense(32, activation='relu'))
    model.add(Dense(actions.shape[0], activation='softmax'))
    model.compile(optimizer='Adam', loss='categorical_crossentropy', metrics=['categorical_accuracy'])
    print('------------------------------------------------------------------------')
    print(f'Training for fold {fold_no} ...')
    history = model.fit(X[train], y[train], epochs=2000, callbacks=[tb_callback, checkpoint])
    scores = model.evaluate(X[test], y[test], verbose=0)
    print(f'Score for fold {fold_no}: {model.metrics_names[0]} of {scores[0]}; {model.metrics_names[1]} of {scores[1]*100}%')
    acc_per_fold.append(scores[1] * 100)
    loss_per_fold.append(scores[0])
    
    # Increase fold number
    fold_no = fold_no + 1
print('------------------------------------------------------------------------')
print('Score per fold')
for i in range(0, len(acc_per_fold)):
  print('------------------------------------------------------------------------')
  print(f'> Fold {i+1} - Loss: {loss_per_fold[i]} - Accuracy: {acc_per_fold[i]}%')
print('------------------------------------------------------------------------')
print('Average scores for all folds:')
print(f'> Accuracy: {np.mean(acc_per_fold)} (+- {np.std(acc_per_fold)})')
print(f'> Loss: {np.mean(loss_per_fold)}')
print('------------------------------------------------------------------------')
    

------------------------------------------------------------------------
Training for fold 1 ...
Epoch 1/2000
3/3 [==============================] - 6s 67ms/step - loss: 1.0971 - categorical_accuracy: 0.3333
Epoch 2/2000
3/3 [==============================] - 0s 72ms/step - loss: 1.0645 - categorical_accuracy: 0.3472
Epoch 3/2000
3/3 [==============================] - 0s 67ms/step - loss: 0.9911 - categorical_accuracy: 0.3611
Epoch 4/2000
3/3 [==============================] - 0s 61ms/step - loss: 0.8010 - categorical_accuracy: 0.6944
Epoch 5/2000
3/3 [==============================] - 0s 60ms/step - loss: 1.2083 - categorical_accuracy: 0.6528
Epoch 6/2000
3/3 [==============================] - 0s 69ms/step - loss: 1.0365 - categorical_accuracy: 0.4861
Epoch 7/2000
3/3 [==============================] - 0s 60ms/step - loss: 0.9333 - categorical_accuracy: 0.5139
Epoch 8/2000
3/3 [==============================] - 0s 57ms/step - loss: 0.8471 - categorical_accuracy: 0.6389
Epoch 9/2000
3/

In [86]:
print(history)

In [69]:
model.fit(X_train, y_train, epochs=2000, callbacks=[tb_callback])

Epoch 1/2000
3/3 [==============================] - 5s 67ms/step - loss: 1.0914 - categorical_accuracy: 0.5059
Epoch 2/2000
3/3 [==============================] - 0s 45ms/step - loss: 1.0909 - categorical_accuracy: 0.5294
Epoch 3/2000
3/3 [==============================] - 0s 52ms/step - loss: 1.0272 - categorical_accuracy: 0.3765
Epoch 4/2000
3/3 [==============================] - 0s 48ms/step - loss: 0.9633 - categorical_accuracy: 0.5412
Epoch 5/2000
3/3 [==============================] - 0s 54ms/step - loss: 0.8463 - categorical_accuracy: 0.6706
Epoch 6/2000
3/3 [==============================] - 0s 50ms/step - loss: 0.7040 - categorical_accuracy: 0.6353
Epoch 7/2000
3/3 [==============================] - 0s 45ms/step - loss: 0.8341 - categorical_accuracy: 0.6588
Epoch 8/2000
3/3 [==============================] - 0s 54ms/step - loss: 0.6896 - categorical_accuracy: 0.7176
Epoch 9/2000
3/3 [==============================] - 0s 55ms/step - loss: 0.6167 - categorical_accuracy: 0.6471
E

In [83]:
res = model.predict(X_test)
actions[np.argmax(res[4])]

1/1 [==============================] - 1s 708ms/step


'hello'

In [44]:
model.save('action.h5')

In [ ]:
del model

In [ ]:
model.load_weights('action.h5')

In [ ]:
converter = tf.lite.TFLiteConverter.from_keras_model(model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
converter.experimental_new_converter=True
converter.target_spec.supported_ops = [tf.lite.OpsSet.TFLITE_BUILTINS,
tf.lite.OpsSet.SELECT_TF_OPS]
tflite_model = converter.convert()

# Save the TensorFlow Lite model to a file
with open('pose.tflite', 'wb') as f:
    f.write(tflite_model)

In [45]:
from sklearn.metrics import multilabel_confusion_matrix, accuracy_score

In [84]:
yhat = model.predict(X_test)
print(X_test.shape)
print(yhat)
ytrue = np.argmax(y_test, axis=1).tolist()
yhat = np.argmax(yhat, axis=1).tolist()
multilabel_confusion_matrix(ytrue, yhat)

1/1 [==============================] - 0s 64ms/step
(5, 30, 99)
[[3.8740627e-10 1.9852092e-07 9.9999976e-01]
 [6.2904570e-13 9.9161410e-01 8.3859358e-03]
 [0.0000000e+00 1.0000000e+00 0.0000000e+00]
 [2.0259204e-06 7.9733320e-07 9.9999714e-01]
 [1.0000000e+00 7.5919980e-17 1.0514919e-13]]


array([[[4, 0],
        [0, 1]],

       [[3, 0],
        [0, 2]],

       [[3, 0],
        [0, 2]]], dtype=int64)

In [72]:
accuracy_score(ytrue, yhat)

1.0

In [48]:
from scipy import stats

In [49]:
colors = [(245,117,16), (117,245,16), (16,117,245)]
def prob_viz(res, actions, input_frame, colors):
    output_frame = input_frame.copy()
    for num, prob in enumerate(res):
        cv2.rectangle(output_frame, (0,60+num*40), (int(prob*100), 90+num*40), colors[num], -1)
        cv2.putText(output_frame, actions[num], (0, 85+num*40), cv2.FONT_HERSHEY_SIMPLEX, 1, (255,255,255), 2, cv2.LINE_AA)
        
    return output_frame

In [ ]:
plt.figure(figsize=(18,18))
plt.imshow(prob_viz(res, actions, image, colors))

In [85]:
# 1. New detection variables
sequence = []
sentence = []
predictions = []
threshold = 0.75

cap = cv2.VideoCapture(0)
# Set mediapipe model 
with mp_pose.Pose(min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
    while cap.isOpened():

        # Read feed
        ret, frame = cap.read()

        # Make detections
        image, results = mediapipe_detection(frame, pose)
        print(results)
        
        # Draw landmarks
        draw_landmarks(image, results)
        
        # 2. Prediction logic
        keypoints = extract_keypoints(results)
        sequence.append(keypoints)
        sequence = sequence[-30:]
        
        if len(sequence) == 30:
            res = model.predict(np.expand_dims(sequence, axis=0))[0]
            print(actions[np.argmax(res)])
            predictions.append(np.argmax(res))
            
            
        #3. Viz logic
            
            if res[np.argmax(res)] > threshold: 
                
                if len(sentence) > 0: 
                    if actions[np.argmax(res)] != sentence[-1]:
                        sentence.append(actions[np.argmax(res)])
                else:
                    sentence.append(actions[np.argmax(res)])

            if len(sentence) > 5: 
                sentence = sentence[-5:]

            # Viz probabilities
            image = prob_viz(res, actions, image, colors)
            
        cv2.rectangle(image, (0,0), (640, 40), (245, 117, 16), -1)
        cv2.putText(image, ' '.join(sentence), (3,30), 
                       cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 255, 255), 2, cv2.LINE_AA)
        
        # Show to screen
        cv2.imshow('OpenCV Feed', image)

        # Break gracefully
        if cv2.waitKey(10) & 0xFF == ord('q'):
            break
    cap.release()
    cv2.destroyAllWindows()

<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.solution_base.SolutionOutputs'>
<class 'mediapipe.python.soluti

In [ ]:
import tensorflow as tf

model = tf.keras.models.load_model('action.h5')

# Convert to TensorFlow Lite without quantization
converter = tf.lite.TFLiteConverter.from_keras_model(model)
tflite_model = converter.convert()

# Apply post-conversion quantization
converter = tf.lite.TFLiteConverter.from_keras_model(model)
converter.optimizations = [tf.lite.Optimize.DEFAULT]
tflite_quantized_model = converter.convert()